## BUILDING A HEART DISEASE CLASSIFIER CONTINUED



### HYPERPARAMETER TUNNING


All models are performing at an accuracy between `76` and `83 percent` on the heart disease dataset so far, which is pretty fine though not good enough for deployment. additional `hyperparameter tunning` for some of these models can be embarked on to see if I can grind out better results from them.


### Data Preparation

In [1]:
import pandas as pd
import numpy as np


df = pd.read_csv('heart-disease.csv')
df.head()

age  sex  cp  trestbps  chol  fbs  restecg  thalach  exang  oldpeak  slope  \
0   63    1   3       145   233    1        0      150      0      2.3      0   
1   37    1   2       130   250    0        1      187      0      3.5      0   
2   41    0   1       130   204    0        0      172      0      1.4      2   
3   56    1   1       120   236    0        1      178      0      0.8      2   
4   57    0   0       120   354    0        1      163      1      0.6      2   

   ca  thal  target  
0   0     1       1  
1   0     2       1  
2   0     2       1  
3   0     2       1  
4   0     2       1

In [3]:
X = df[['age', 'sex', 'cp', 'trestbps', 
        'chol', 'fbs', 'restecg', 'thalach', 'exang', 'oldpeak', 'slope', 'ca', 'thal']].values
y = df['target'].values

feature_names = ['age', 'sex', 'cp', 'trestbps', 
        'chol', 'fbs', 'restecg', 'thalach', 'exang', 'oldpeak', 'slope', 'ca', 'thal']

X




# NORMALIZING THE DATASET FOR SOME OF THE MACHINE LEARNING MODELS
from sklearn.preprocessing import StandardScaler

scale = StandardScaler()
X_scaled = scale.fit_transform(X)
X_scaled


##### Data Preparation (Spliiting scaled_X and y into trainining and validation sets)
from sklearn.model_selection import train_test_split

np.random.seed(42)

X_scaled = X_scaled
y = y

X_train, X_test, y_train, y_test = train_test_split(X_scaled, y, test_size=0.25)

print(f"X_train: {len(X_train)}, X_test: {len(X_test)}, y_train: {len(y_train)}, y_test: {len(y_test)}")

X_train: 227, X_test: 76, y_train: 227, y_test: 76


In [10]:
# Evaluation function for the models

from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score



def evaluate_preds(y_true, y_preds):
    """
    Performs evaluation comparison on y_true labels and y_preds labels on a classification model
    """
    accuracy = accuracy_score(y_true, y_preds)
    precision = precision_score(y_true, y_preds)
    recall = recall_score(y_true, y_preds)
    f1 = f1_score(y_true, y_preds)
    metric_dict = {"accuracy": round(accuracy, 2),
                   "precision": round(precision, 2),
                   "recall": round(recall, 2),
                   "F1": round(f1, 2)}
    print(f"Accuracy: {accuracy * 100:.2f}%")
    print(f"Precision: {precision * 100:.2f}")
    print(f"Recall: {recall * 100:.2f}")
    print(f"F1 score: {f1 * 100:.2f}")
    
    return metric_dict

#### Tunning Random Forest Classifier Using RandomizedSearchCV

In [15]:
from sklearn.model_selection import RandomizedSearchCV


clf = RandomForestClassifier(n_jobs=1)

#Hyperparameter grid for RandomForestClassifier
rf_grid = {"n_estimators": np.arange(10, 1000, 50),
           "max_depth": [None, 10, 20, 30, 40, 50, 60, 70, 80, 90, 100],
           "min_samples_split": np.arange(2, 20, 2),
           "min_samples_leaf": np.arange(1, 20, 2),
           "bootstrap": [True, False]}


rs_clf = RandomizedSearchCV(estimator=clf, param_distributions=rf_grid, n_iter=100, cv=3, random_state=42, verbose=True)

rs_clf.fit(X_train, y_train)

Fitting 3 folds for each of 100 candidates, totalling 300 fits


RandomizedSearchCV(cv=3, estimator=RandomForestClassifier(n_jobs=1), n_iter=100,
                   param_distributions={'bootstrap': [True, False],
                                        'max_depth': [None, 10, 20, 30, 40, 50,
                                                      60, 70, 80, 90, 100],
                                        'min_samples_leaf': array([ 1,  3,  5,  7,  9, 11, 13, 15, 17, 19]),
                                        'min_samples_split': array([ 2,  4,  6,  8, 10, 12, 14, 16, 18]),
                                        'n_estimators': array([ 10,  60, 110, 160, 210, 260, 310, 360, 410, 460, 510, 560, 610,
       660, 710, 760, 810, 860, 910, 960])},
                   random_state=42, verbose=True)

In [18]:
print(rs_clf.best_params_)
print("--------------------")
preds = rs_clf.predict(X_test)
rs_metrics = evaluate_preds(y_test, preds)

{'n_estimators': 660, 'min_samples_split': 14, 'min_samples_leaf': 17, 'max_depth': 80, 'bootstrap': False}
--------------------
Accuracy: 84.21%
Precision: 82.22
Recall: 90.24
F1 score: 86.05


###### There is a slight improvement in the perfromance of the Random Forest Classifier from 82 percent to 84 percent


#### Tunning  RandomForestClassifier with GridSearchCV

In [26]:
from sklearn.model_selection import GridSearchCV


clf = RandomForestClassifier(n_jobs=1)

#Hyperparameter grid for RandomForestClassifier
rf_grid  = {"n_estimators": [100, 200, 400, 600],
           "max_depth": [10, 30, 60, 80, 100],
           "min_samples_split": [2, 6, 10, 20],
           "min_samples_leaf": [3, 7, 14, 23]
           }


rs_clf = GridSearchCV(estimator=clf, param_grid=rf_grid, cv=3, verbose=True)

rs_clf.fit(X_train, y_train)

Fitting 3 folds for each of 320 candidates, totalling 960 fits


GridSearchCV(cv=3, estimator=RandomForestClassifier(n_jobs=1),
             param_grid={'max_depth': [10, 30, 60, 80, 100],
                         'min_samples_leaf': [3, 7, 14, 23],
                         'min_samples_split': [2, 6, 10, 20],
                         'n_estimators': [100, 200, 400, 600]},
             verbose=True)

In [27]:
print(rs_clf.best_params_)
print("--------------------")
preds = rs_clf.predict(X_test)
rs_metrics = evaluate_preds(y_test, preds)

{'max_depth': 10, 'min_samples_leaf': 14, 'min_samples_split': 10, 'n_estimators': 100}
--------------------
Accuracy: 84.21%
Precision: 82.22
Recall: 90.24
F1 score: 86.05


##### After the grid search through the features, the accuracy of the RandomForestClassifier remained at 84 percent
#### Tunning LogisticRegression with RandomizedSearchCV

In [44]:
from sklearn.linear_model import LogisticRegression
np.random.seed(42)

clf = LogisticRegression(n_jobs=1)


log_reg_grid = {"C": np.logspace(-4, 4, 20),
                "solver": ["liblinear", 'lbfgs', 'newton'],
                "penalty": ['none', 'l1', 'l2', 'elasticent'], }

log__reg_clf = RandomizedSearchCV(estimator=clf, param_distributions=log_reg_grid, n_iter=30, cv=5, verbose=True)

log__reg_clf.fit(X_train, y_train)

Fitting 5 folds for each of 30 candidates, totalling 150 fits


C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py", line 1306, in fit
    solver = _check_solver(self.solver, self.penalty, self.dual)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py", line 454, in _check_solver
    raise ValueError(
ValueError: penalty='none' is not supported for the liblinear solver

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. T

C:\Users\kizito\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py:1322: UserWarning: Setting penalty='none' will ignore the C and l1_ratio parameters
  warnings.warn(
C:\Users\kizito\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py:1322: UserWarning: Setting penalty='none' will ignore the C and l1_ratio parameters
  warnings.warn(
C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py", line 1306, in fit
    solver = _check_solver(self.solver, self.penalty, self.dual)
  File "C:\Users\kizito\anaconda3\lib\site-pack

C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py", line 1306, in fit
    solver = _check_solver(self.solver, self.penalty, self.dual)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py", line 434, in _check_solver
    raise ValueError("Logistic Regression supports only solvers in %s, got"
ValueError: Logistic Regression supports only solvers in ['liblinear', 'newton-cg', 'lbfgs', 'sag', 'saga'], got newton.

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\kizito\anacond

RandomizedSearchCV(cv=5, estimator=LogisticRegression(n_jobs=1), n_iter=30,
                   param_distributions={'C': array([1.00000000e-04, 2.63665090e-04, 6.95192796e-04, 1.83298071e-03,
       4.83293024e-03, 1.27427499e-02, 3.35981829e-02, 8.85866790e-02,
       2.33572147e-01, 6.15848211e-01, 1.62377674e+00, 4.28133240e+00,
       1.12883789e+01, 2.97635144e+01, 7.84759970e+01, 2.06913808e+02,
       5.45559478e+02, 1.43844989e+03, 3.79269019e+03, 1.00000000e+04]),
                                        'penalty': ['none', 'l1', 'l2',
                                                    'elasticent'],
                                        'solver': ['liblinear', 'lbfgs',
                                                   'newton']},
                   verbose=True)

In [49]:
print(log__reg_clf.best_params_)
print("--------------------")
preds = log__reg_clf.predict(X_test)
rs_metrics = evaluate_preds(y_test, preds)

{'solver': 'liblinear', 'penalty': 'l2', 'C': 0.0001}
--------------------
Accuracy: 86.84%
Precision: 86.05
Recall: 90.24
F1 score: 88.10


##### Logistic Regression model accuracy improved from 81 percent to 86.84 percent after RandomizedSearchCV training


#### Tunning Logistic Regression with GridSearchCV

In [51]:
from sklearn.linear_model import LogisticRegression

np.random.seed(42)

clf = LogisticRegression(n_jobs=1)


log_reg_grid = {"C": np.logspace(-4, 4, 20),
                "solver": ["liblinear"],
                "penalty": ['none', 'l1', 'l2', 'elasticent'], }

log_reg_clf = GridSearchCV(estimator=clf, param_grid=log_reg_grid, cv=5, verbose=True)

log_reg_clf.fit(X_train, y_train)

Fitting 5 folds for each of 80 candidates, totalling 400 fits


C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py", line 1306, in fit
    solver = _check_solver(self.solver, self.penalty, self.dual)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py", line 454, in _check_solver
    raise ValueError(
ValueError: penalty='none' is not supported for the liblinear solver

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. T

C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py", line 1306, in fit
    solver = _check_solver(self.solver, self.penalty, self.dual)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py", line 454, in _check_solver
    raise ValueError(
ValueError: penalty='none' is not supported for the liblinear solver

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. T

C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py", line 1306, in fit
    solver = _check_solver(self.solver, self.penalty, self.dual)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py", line 439, in _check_solver
    raise ValueError("Logistic Regression supports only penalties in %s,"
ValueError: Logistic Regression supports only penalties in ['l1', 'l2', 'elasticnet', 'none'], got elasticent.

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\kizito\anaconda3\lib\site-

C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py", line 1306, in fit
    solver = _check_solver(self.solver, self.penalty, self.dual)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py", line 454, in _check_solver
    raise ValueError(
ValueError: penalty='none' is not supported for the liblinear solver

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. T

GridSearchCV(cv=5, estimator=LogisticRegression(n_jobs=1),
             param_grid={'C': array([1.00000000e-04, 2.63665090e-04, 6.95192796e-04, 1.83298071e-03,
       4.83293024e-03, 1.27427499e-02, 3.35981829e-02, 8.85866790e-02,
       2.33572147e-01, 6.15848211e-01, 1.62377674e+00, 4.28133240e+00,
       1.12883789e+01, 2.97635144e+01, 7.84759970e+01, 2.06913808e+02,
       5.45559478e+02, 1.43844989e+03, 3.79269019e+03, 1.00000000e+04]),
                         'penalty': ['none', 'l1', 'l2', 'elasticent'],
                         'solver': ['liblinear']},
             verbose=True)

In [52]:
print(log_reg_clf.best_params_)
print("--------------------")
preds = log_reg_clf.predict(X_test)
rs_metrics = evaluate_preds(y_test, preds)

{'C': 0.0001, 'penalty': 'l2', 'solver': 'liblinear'}
--------------------
Accuracy: 86.84%
Precision: 86.05
Recall: 90.24
F1 score: 88.10


##### LogisticRegression accuracy remains at approximately 87 percent after GridSearchCV

### Tunning KneighborsClassifier with RandomizedSearchCV

In [2]:
import numpy as np

np.arange(11, 111, 10)

array([ 11,  21,  31,  41,  51,  61,  71,  81,  91, 101])

In [15]:
#### Tunning KNeighborsClassifier with RandomizedSearchCV
from sklearn.model_selection import RandomizedSearchCV

clf = KNeighborsClassifier(n_jobs=-1)

#Hyperparameter grid for RandomForestClassifier
kn_grid = {"n_neighbors": np.arange(11, 111, 10),
           "weights": ['uniform', 'Distance'],
           "metric": ["Euvlidean", "manhanttan", "minkowski"]
           }




kn_clf = RandomizedSearchCV(estimator=clf, param_distributions=kn_grid, n_iter=30, cv=5, verbose=True)

kn_clf.fit(X_train, y_train)

Fitting 5 folds for each of 30 candidates, totalling 150 fits


C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:683: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 674, in _score
    scores = scorer(estimator, X_test, y_test)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\metrics\_scorer.py", line 397, in _passthrough_scorer
    return estimator.score(*args, **kwargs)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\base.py", line 500, in score
    return accuracy_score(y, self.predict(X), sample_weight=sample_weight)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\neighbors\_classification.py", line 206, in predict
    weights = _get_weights(neigh_dist, self.weights)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\neighbors\_base.py", line 111, in _get_weights
    

C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\neighbors\_classification.py", line 179, in fit
    return self._fit(X, y)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\neighbors\_base.py", line 399, in _fit
    self._check_algorithm_metric()
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\neighbors\_base.py", line 342, in _check_algorithm_metric
    raise ValueError("Metric '%s' not valid. Use "
ValueError: Metric 'Euvlidean' not valid. Use sorted(sklearn.neighbors.VALID_METRICS['brute']) to get valid options. Metric can also be a 

C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:683: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 674, in _score
    scores = scorer(estimator, X_test, y_test)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\metrics\_scorer.py", line 397, in _passthrough_scorer
    return estimator.score(*args, **kwargs)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\base.py", line 500, in score
    return accuracy_score(y, self.predict(X), sample_weight=sample_weight)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\neighbors\_classification.py", line 206, in predict
    weights = _get_weights(neigh_dist, self.weights)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\neighbors\_base.py", line 111, in _get_weights
    

C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\neighbors\_classification.py", line 179, in fit
    return self._fit(X, y)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\neighbors\_base.py", line 399, in _fit
    self._check_algorithm_metric()
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\neighbors\_base.py", line 342, in _check_algorithm_metric
    raise ValueError("Metric '%s' not valid. Use "
ValueError: Metric 'manhanttan' not valid. Use sorted(sklearn.neighbors.VALID_METRICS['brute']) to get valid options. Metric can also be a

RandomizedSearchCV(cv=5, estimator=KNeighborsClassifier(n_jobs=-1), n_iter=30,
                   param_distributions={'metric': ['Euvlidean', 'manhanttan',
                                                   'minkowski'],
                                        'n_neighbors': array([ 11,  21,  31,  41,  51,  61,  71,  81,  91, 101]),
                                        'weights': ['uniform', 'Distance']},
                   verbose=True)

In [16]:
print(kn_clf.best_params_)
print("--------------------")
preds = kn_clf.predict(X_test)
rs_metrics = evaluate_preds(y_test, preds)

{'weights': 'uniform', 'n_neighbors': 11, 'metric': 'minkowski'}
--------------------
Accuracy: 86.84%
Precision: 87.80
Recall: 87.80
F1 score: 87.80


##### KNN improved  from 81 percent accuracy to 86.84 percent after RandomizedSearchCV training

### Tunning KneighborsClassifier With GridSearchCV

In [17]:
from sklearn.model_selection import GridSearchCV

clf = KNeighborsClassifier(n_jobs=-1)

#Hyperparameter grid for RandomForestClassifier
kn_grid = {"n_neighbors": np.arange(11, 31, 10),
           "weights": ['uniform', 'Distance'],
           "metric": ["minkowski"]
           }




kn_clf = GridSearchCV(estimator=clf, param_grid=kn_grid, cv=5, verbose=True)

kn_clf.fit(X_train, y_train)

Fitting 5 folds for each of 4 candidates, totalling 20 fits


C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:683: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 674, in _score
    scores = scorer(estimator, X_test, y_test)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\metrics\_scorer.py", line 397, in _passthrough_scorer
    return estimator.score(*args, **kwargs)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\base.py", line 500, in score
    return accuracy_score(y, self.predict(X), sample_weight=sample_weight)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\neighbors\_classification.py", line 206, in predict
    weights = _get_weights(neigh_dist, self.weights)
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\neighbors\_base.py", line 111, in _get_weights
    

GridSearchCV(cv=5, estimator=KNeighborsClassifier(n_jobs=-1),
             param_grid={'metric': ['minkowski'],
                         'n_neighbors': array([11, 21]),
                         'weights': ['uniform', 'Distance']},
             verbose=True)

In [18]:
print(kn_clf.best_params_)
print("--------------------")
preds = kn_clf.predict(X_test)
rs_metrics = evaluate_preds(y_test, preds)

{'metric': 'minkowski', 'n_neighbors': 11, 'weights': 'uniform'}
--------------------
Accuracy: 86.84%
Precision: 87.80
Recall: 87.80
F1 score: 87.80


##### KNN stayed at 86.84 percent after GridSearchCV training

### Tunning Xgboost Classifer using Randomized SearchCV

In [21]:
clf = XGBClassifier(n_jobs=-1)


param_grid = {
    "max_depth": [3, 4, 5, 7],
    "learning_rate": [0.001, 0.02, 0.03],
    "gamma": [0, 0.25, 1],
    "reg_lambda": [0, 1, 10],
    "scale_pos_weight": [1, 3, 5],
    "subsample": [0.8],
    "colsample_bytree": [0.5],
    "objective": ['multi:softmax', 'reg:linear'], 
    "num_class": [2]
}




xgb_clf = RandomizedSearchCV(estimator=clf, param_distributions=param_grid, n_iter=30, cv=5, verbose=True)

xgb_clf.fit(X_train, y_train)

Fitting 5 folds for each of 30 candidates, totalling 150 fits
[19:03:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/objective/regression_obj.cu:188: reg:linear is now deprecated in favor of reg:squarederror.


C:\Users\kizito\anaconda3\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\kizito\anaconda3\lib\site-packages\xgboost\core.py", line 506, in inner_f
    return f(**kwargs)
  File 

[19:03:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/objective/regression_obj.cu:188: reg:linear is now deprecated in favor of reg:squarederror.
[19:03:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/objective/regression_obj.cu:188: reg:linear is now deprecated in favor of reg:squarederror.
[19:03:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/objective/regression_obj.cu:188: reg:linear is now deprecated in favor of reg:squarederror.
[19:03:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/objective/regression_obj.cu:188: reg:linear is now deprecated in favor of reg:squarederror.
[19:03:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:576: 
Parameters: { "scale_pos_weight" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoos

C:\Users\kizito\anaconda3\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[19:03:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:576: 
Parameters: { "scale_pos_weight" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[19:03:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softmax' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


...

C:\Users\kizito\anaconda3\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[19:04:09] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:576: 
Parameters: { "scale_pos_weight" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[19:04:09] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softmax' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_search.py:918: UserWarning: One or more of the test scores are non-finite: [       nan 0.81497585        nan 0.83246377        nan        nan
 0.82811594 0.82792271        nan        nan 0.82792271        nan
 0.81942029        nan 0.83681159 0.8236715  0.81913043        nan
 0.82811594        nan 0.82792271        nan 0.83246377 0.82792271
 0.83681159        nan        nan 0.82801932        nan 0.82801932]
  warnings.warn(
C:\Users\kizito\anaconda3\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[19:04:10] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:576: 
Parameters: { "scale_pos_weight" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[19:04:10] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softmax' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


RandomizedSearchCV(cv=5,
                   estimator=XGBClassifier(base_score=None, booster=None,
                                           colsample_bylevel=None,
                                           colsample_bynode=None,
                                           colsample_bytree=None,
                                           enable_categorical=False, gamma=None,
                                           gpu_id=None, importance_type=None,
                                           interaction_constraints=None,
                                           learning_rate=None,
                                           max_delta_step=None, max_depth=None,
                                           min_child_weight=None, missing=nan,
                                           monotone_constraints...
                                           scale_pos_weight=None,
                                           subsample=None, tree_method=None,
                                      

In [22]:
print(xgb_clf.best_params_)
print("--------------------")
preds = xgb_clf.predict(X_test)
rs_metrics = evaluate_preds(y_test, preds)

{'subsample': 0.8, 'scale_pos_weight': 1, 'reg_lambda': 0, 'objective': 'multi:softmax', 'num_class': 2, 'max_depth': 4, 'learning_rate': 0.02, 'gamma': 0.25, 'colsample_bytree': 0.5}
--------------------
Accuracy: 82.89%
Precision: 83.33
Recall: 85.37
F1 score: 84.34


##### Xgboost Classifier imporoved  from 79 percent accuracy to 82.89 percent after RandomizedSearchCV training

### Tunning Xgboost Classifer using GridSearchCV

In [23]:
clf = XGBClassifier(n_jobs=-1)


param_grid = {
    "max_depth": [3, 4, 5, 7],
    "learning_rate": [0.001, 0.02, 0.03],
    "gamma": [0, 0.25, 1],
    "reg_lambda": [0, 1, 10],
    "scale_pos_weight": [1, 3, 5],
    "subsample": [0.8],
    "colsample_bytree": [0.5],
    "objective": ['multi:softmax', 'reg:linear'], 
    "num_class": [2]
}




xgb_clf = GridSearchCV(estimator=clf, param_grid=param_grid, cv=5, verbose=True)

xgb_clf.fit(X_train, y_train)

Fitting 5 folds for each of 648 candidates, totalling 3240 fits
[20:28:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:576: 
Parameters: { "scale_pos_weight" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[20:28:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softmax' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


C:\Users\kizito\anaconda3\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\kizito\anaconda3\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[20:28:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:576: 
Parameters: { "scale_pos_weight" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[20:28:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softmax' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


C:\Users\kizito\anaconda3\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[20:28:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:576: 
Parameters: { "scale_pos_weight" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[20:28:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softmax' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


...

C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\kizito\anaconda3\lib\site-packages\xgboost\core.py", line 506, in inner_f
    return f(**kwargs)
  File "C:\Users\kizito\anaconda3\lib\site-packages\xgboost\sklearn.py", line 1250, in fit
    self._Booster = train(
  File "C:\Users\kizito\anaconda3\lib\site-packages\xgboost\training.py", line 188, in train
    bst = _train_internal(params, dtrain,
  File "C:\Users\kizito\anaconda3\lib\site-packages\xgboost\training.py", line 81, in _train_internal
    bst.update(dtrain, i, obj)
  File "C:\Users\kizito\anaconda3\lib\site-packages\xgboost\core.py", line 1

[20:36:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/objective/regression_obj.cu:188: reg:linear is now deprecated in favor of reg:squarederror.
[20:36:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/objective/regression_obj.cu:188: reg:linear is now deprecated in favor of reg:squarederror.
[20:36:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/objective/regression_obj.cu:188: reg:linear is now deprecated in favor of reg:squarederror.
[20:36:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/objective/regression_obj.cu:188: reg:linear is now deprecated in favor of reg:squarederror.
[20:36:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/objective/regression_obj.cu:188: reg:linear is now deprecated in favor of reg:squarederror.
[20:36:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/objective/regression_obj.cu:18

C:\Users\kizito\anaconda3\lib\site-packages\sklearn\model_selection\_search.py:918: UserWarning: One or more of the test scores are non-finite: [0.82792271 0.82792271 0.82792271 0.83236715 0.83236715 0.83236715
 0.8236715  0.8236715  0.8236715         nan        nan        nan
        nan        nan        nan        nan        nan        nan
 0.82801932 0.82801932 0.82801932 0.82801932 0.82801932 0.82801932
 0.8236715  0.8236715  0.8236715         nan        nan        nan
        nan        nan        nan        nan        nan        nan
 0.82801932 0.82801932 0.82801932 0.82801932 0.82801932 0.82801932
 0.8236715  0.8236715  0.8236715         nan        nan        nan
        nan        nan        nan        nan        nan        nan
 0.83246377 0.83246377 0.83246377 0.82801932 0.82801932 0.82801932
 0.8236715  0.8236715  0.8236715         nan        nan        nan
        nan        nan        nan        nan        nan        nan
 0.82347826 0.82347826 0.82347826 0.82792271 0.82792

[20:36:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:576: 
Parameters: { "scale_pos_weight" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[20:36:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softmax' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


GridSearchCV(cv=5,
             estimator=XGBClassifier(base_score=None, booster=None,
                                     colsample_bylevel=None,
                                     colsample_bynode=None,
                                     colsample_bytree=None,
                                     enable_categorical=False, gamma=None,
                                     gpu_id=None, importance_type=None,
                                     interaction_constraints=None,
                                     learning_rate=None, max_delta_step=None,
                                     max_depth=None, min_child_weight=None,
                                     missing=nan, monotone_constraints=None,...
                                     reg_lambda=None, scale_pos_weight=None,
                                     subsample=None, tree_method=None,
                                     validate_parameters=None, verbosity=None),
             param_grid={'colsample_bytree': [0.5], 'gam

In [25]:
print(xgb_clf.best_params_)
print("--------------------")
preds = xgb_clf.predict(X_test)
rs_metrics = evaluate_preds(y_test, preds)

{'colsample_bytree': 0.5, 'gamma': 0.25, 'learning_rate': 0.03, 'max_depth': 5, 'num_class': 2, 'objective': 'multi:softmax', 'reg_lambda': 1, 'scale_pos_weight': 1, 'subsample': 0.8}
--------------------
Accuracy: 84.21%
Precision: 83.72
Recall: 87.80
F1 score: 85.71


##### Xgboost Classifier imporoved further to 84.21 percent after GridSearchCV training

### Tunning Support Vector Machines

In [62]:
from sklearn.svm import SVC

model1 = SVC(kernel='sigmoid',degree=1, C=1.0)
model2 = SVC(kernel='sigmoid',degree=2, C=0.8)
model3 = SVC(kernel='sigmoid',degree=3, C=0.6)
model4 = SVC(kernel='sigmoid',degree=4, C=0.2)
               
models = [model1, model2, model3, model4]

summary = {}

for model in models:
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    metrics = evaluate_preds(y_test, pred)
    summary[model] = metrics

Accuracy: 88.16%
Precision: 88.10
Recall: 90.24
F1 score: 89.16
Accuracy: 86.84%
Precision: 86.05
Recall: 90.24
F1 score: 88.10
Accuracy: 86.84%
Precision: 86.05
Recall: 90.24
F1 score: 88.10
Accuracy: 86.84%
Precision: 86.05
Recall: 90.24
F1 score: 88.10


In [58]:
summary

{SVC(degree=1, kernel='sigmoid'): {'accuracy': 0.88,
  'precision': 0.88,
  'recall': 0.9,
  'F1': 0.89},
 SVC(C=0.8, degree=2, kernel='sigmoid'): {'accuracy': 0.87,
  'precision': 0.86,
  'recall': 0.9,
  'F1': 0.88},
 SVC(C=0.6, kernel='sigmoid'): {'accuracy': 0.87,
  'precision': 0.86,
  'recall': 0.9,
  'F1': 0.88},
 SVC(C=0.2, degree=4, kernel='sigmoid'): {'accuracy': 0.87,
  'precision': 0.86,
  'recall': 0.9,
  'F1': 0.88}}

##### The SVC(sigmoid kernel, degree=3, and C=1.0) gets an improved score of 83 percent to 88 percent

In [64]:
model1 = SVC(kernel='rbf', probability=True, C=1.0)
model2 = SVC(kernel='rbf', probability=True, C=0.8)
model3 = SVC(kernel='rbf', probability=True, C=0.6)
model4 = SVC(kernel='rbf', probability=True, C=0.2)
               
models = [model1, model2, model3, model4]

summary = {}

for model in models:
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    metrics = evaluate_preds(y_test, pred)
    summary[model] = metrics

Accuracy: 88.16%
Precision: 88.10
Recall: 90.24
F1 score: 89.16
Accuracy: 89.47%
Precision: 88.37
Recall: 92.68
F1 score: 90.48
Accuracy: 89.47%
Precision: 88.37
Recall: 92.68
F1 score: 90.48
Accuracy: 89.47%
Precision: 88.37
Recall: 92.68
F1 score: 90.48


In [65]:
summary

{SVC(probability=True): {'accuracy': 0.88,
  'precision': 0.88,
  'recall': 0.9,
  'F1': 0.89},
 SVC(C=0.8, probability=True): {'accuracy': 0.89,
  'precision': 0.88,
  'recall': 0.93,
  'F1': 0.9},
 SVC(C=0.6, probability=True): {'accuracy': 0.89,
  'precision': 0.88,
  'recall': 0.93,
  'F1': 0.9},
 SVC(C=0.2, probability=True): {'accuracy': 0.89,
  'precision': 0.88,
  'recall': 0.93,
  'F1': 0.9}}

##### The SVC(rbf kernel, prbability=True, and C=0.8) gets an improved score of 83 percent to 89 percent

In [68]:
model1 = SVC(kernel='poly', probability=True, C=1.0, degree=1)
model2 = SVC(kernel='poly', probability=True, C=0.8, degree=2)
model3 = SVC(kernel='poly', probability=True, C=0.6, degree=3)
model4 = SVC(kernel='poly', probability=True, C=0.2, degree=4)
               
models = [model1, model2, model3, model4]

summary = {}

for model in models:
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    metrics = evaluate_preds(y_test, pred)
    summary[model] = metrics

Accuracy: 86.84%
Precision: 84.44
Recall: 92.68
F1 score: 88.37
Accuracy: 72.37%
Precision: 71.74
Recall: 80.49
F1 score: 75.86
Accuracy: 88.16%
Precision: 88.10
Recall: 90.24
F1 score: 89.16
Accuracy: 61.84%
Precision: 58.82
Recall: 97.56
F1 score: 73.39


In [69]:
summary

{SVC(degree=1, kernel='poly', probability=True): {'accuracy': 0.87,
  'precision': 0.84,
  'recall': 0.93,
  'F1': 0.88},
 SVC(C=0.8, degree=2, kernel='poly', probability=True): {'accuracy': 0.72,
  'precision': 0.72,
  'recall': 0.8,
  'F1': 0.76},
 SVC(C=0.6, kernel='poly', probability=True): {'accuracy': 0.88,
  'precision': 0.88,
  'recall': 0.9,
  'F1': 0.89},
 SVC(C=0.2, degree=4, kernel='poly', probability=True): {'accuracy': 0.62,
  'precision': 0.59,
  'recall': 0.98,
  'F1': 0.73}}

##### The SVC(poly kernel, prbability=True, and C=0.6,  degree=3) gets an improved score of 80 percent to 88 percent 

##### SVC(linear kernel) however improved from 82 to 87 percent

##### We then proceed to summarize the experiment in `project-summary-heart-disease-classification.ipynb`